In [1]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import warnings
warnings.filterwarnings('ignore')
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]="1"
import pandas as pd
import numpy as np
from gtda.time_series import SlidingWindow
import matplotlib.pyplot as plt
from tensorflow.python.keras.backend import set_session
import tensorflow as tf
config = tf.compat.v1.ConfigProto() 
config.gpu_options.allow_growth = True  
config.log_device_placement = True  
sess2 = tf.compat.v1.Session(config=config)
set_session(sess2)  
from tensorflow.keras.layers import Dense, MaxPooling1D, Flatten
from tensorflow.keras import Input, Model
from tensorflow.keras.callbacks import ModelCheckpoint
import tensorflow.compat.v1.keras.backend as K
from tensorflow.keras.models import load_model
from tcn import TCN, tcn_full_summary
from tcn import compiled_tcn
from tensorflow.keras.utils import to_categorical
import csv
import random
import itertools
from keras_flops import get_flops
from mango.tuner import Tuner
import time
from tensorflow.keras.losses import MSE
import pickle
from hardware_utils import *
from data_utils import *

Device mapping:
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: NVIDIA GeForce RTX 3090, pci bus id: 0000:21:00.0, compute capability: 8.6



In [2]:
sampling_rate = 100
window_size = 550
stride = 50
epsilon = 0.4
f = '/home/nesl/earable/Earable/Activity_Dataset/' #dataset directory

X_tr, Y_tr, X_test, Y_test = import_auritus_activity_dataset(dataset_folder = f, 
                                use_timestamp=False, 
                                shuffle=True, 
                                window_size = window_size, stride = stride, 
                                return_test_set = True, test_set_size = 300,channels=0)


random_indices = np.random.choice(X_tr.shape[0], size=1000, replace=False)
X_val = X_tr[random_indices,:,:]
Y_val = Y_tr[random_indices,:]
X_tr = np.delete(X_tr,random_indices,axis=0)
Y_tr = np.delete(Y_tr,random_indices,axis=0)

print(X_tr.shape)
print(Y_tr.shape)
print(X_val.shape)
print(Y_val.shape)
print(X_test.shape)
print(Y_test.shape)

100%|█████████████████████████████████████████| 399/399 [00:11<00:00, 33.47it/s]


(13671, 550, 6)
(13671, 9)
(1000, 550, 6)
(1000, 9)
(300, 550, 6)
(300, 9)


In [3]:
def fgsm_attack(model, image, label, eps):
    image = tf.cast(image, tf.float32)
    with tf.GradientTape() as tape:
        tape.watch(image)
        pred = model(image)
        loss = MSE(label, pred)
        gradient = tape.gradient(loss, image)
        signedGrad = tf.sign(gradient)
        adversary = (image + (signedGrad * eps)).numpy()
        return adversary
    
def perform_fgsm_attack(data,lab,eps,my_model):
    countadv = 0
    for i in tqdm(range(len(data))):
        act = data[i,:,:].reshape(1,data.shape[1],data.shape[2])
        label = lab[i,:]
        actPred = my_model.predict(act)
        actPred = actPred.argmax()
        adversary = fgsm_attack(my_model,act, label, eps=eps)
        pred = my_model.predict(adversary)
        adversaryPred = pred[0].argmax()
        if actPred == adversaryPred:
            countadv += 1
        
 
    adv_accu = countadv / len(data)
    return adv_accu

In [4]:
dirpath="/home/nesl/Mbed Programs/auritus_tcn/" #hardware program directory - this is where the TCN deployment code is stored
device = "NUCLEO_L476RG" #which hardware to use
model_name = 'Auritus_adv'+device+'.hdf5'
HIL = False #use real hardware or proxy?
quantization = False #use quantization or not?
model_epochs = 500 #epochs to train each model for
NAS_epochs = 50 #epochs for hyperparameter tuning
output_name = 'g_model.tflite'
log_file_name = 'TCN_Auritus_adv_'+device+'.csv'
if os.path.exists(log_file_name):
    os.remove(log_file_name)
row_write = ['score', '1-accuracy','adv_accuracy','RAM','Flash','FLOPS','Latency','nb_filters','kernel_size',
             'dilations','use_skip_connections']
with open(log_file_name, 'a', newline='') as csvfile:
    csvwriter = csv.writer(csvfile)
    csvwriter.writerow(row_write)
if os.path.exists(log_file_name[0:-4]+'.p'):
    os.remove(log_file_name[0:-4]+'.p')

In [5]:
def objective_NN(epochs=1000,nb_filters=10,kernel_size=3,
                 dilations=[1, 2, 4, 8, 16, 32, 64, 128, 256],
                 use_skip_connections=True):
    
    err = 'inf'
    adv_accu = 'inf'
    input_dim=X_tr.shape[2]
    
    model = compiled_tcn(return_sequences=False,
                         num_feat=input_dim,
                         num_classes=Y_tr.shape[1],
                         nb_filters=nb_filters,
                         kernel_size=kernel_size,
                         dilations=dilations,
                         nb_stacks=1,
                         max_len=window_size,
                         use_weight_norm=False,
                         use_skip_connections=use_skip_connections)
    
    opt = tf.keras.optimizers.Adam()
    model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
                  optimizer=opt,metrics=['accuracy'])
    Flops = get_flops(model, batch_size=1)
    convert_to_tflite_model(model=model,training_data=X_tr,quantization=quantization,output_name=output_name) 
    maxRAM, maxFlash = return_hardware_specs(device)
    
    if(HIL==True):
        convert_to_cpp_model(dirpath)
        RAM, Flash, Latency, idealArenaSize, errorCode = HIL_controller(dirpath=dirpath,
                                                                       chosen_device=device,
                                                                       window_size=window_size, 
                                                                    number_of_channels = input_dim,
                                                                   quantization=quantization)     
        score = -5.0
        if(Flash==-1):
            row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
            print('Design choice:',row_write)
            with open(log_file_name, 'a', newline='') as csvfile:
                csvwriter = csv.writer(csvfile)
                csvwriter.writerow(row_write)
            return score    
    
        elif(Flash!=-1):
            checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
            model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
                      epochs=epochs,callbacks=[checkpoint],shuffle=True,verbose=1)
            err = 1-checkpoint.best
            adv_accu = perform_fgsm_attack(data=X_val, lab=Y_val,eps=epsilon,my_model=model)
            
            resource_usage = (RAM/maxRAM) + (Flash/maxFlash) 
            score = -err + 0.01*resource_usage - 0.05*Latency - (0.5*(1-adv_accu)) #weigh each component as you like
                
            row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
            print('Design choice:',row_write)
            with open(log_file_name, 'a', newline='') as csvfile:
                csvwriter = csv.writer(csvfile)
                csvwriter.writerow(row_write)   
    else:
        score = -5.0
        Flash = os.path.getsize(output_name)
        RAM = get_model_memory_usage(batch_size=1,model=model)
        Latency=-1
        max_flops = (30e6)
        
        if(RAM < maxRAM and Flash<maxFlash):
            checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
            model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
                      epochs=epochs,callbacks=[checkpoint],shuffle=True,verbose=1)
            err = 1-checkpoint.best 
            adv_accu = perform_fgsm_attack(data=X_val, lab=Y_val,eps=epsilon,my_model=model)
            resource_usage = (RAM/maxRAM) + (Flash/maxFlash)
            score = -err + 0.01*resource_usage - 0.05*(Flops/max_flops)- (0.5*(1-adv_accu))  #weigh each component as you like
        
        row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
        print('Design choice:',row_write)
        with open(log_file_name, 'a', newline='') as csvfile:
            csvwriter = csv.writer(csvfile)
            csvwriter.writerow(row_write) 
    
    return score        

In [6]:
import pickle 

def save_res(data, file_name):
    pickle.dump( data, open( file_name, "wb" ) )
    
min_layer = 3
max_layer = 8
a_list = [1,2,4,8,16,32,64,128,256]
all_combinations = []
dil_list = []
for r in range(len(a_list) + 1):
    combinations_object = itertools.combinations(a_list, r)
    combinations_list = list(combinations_object)
    all_combinations += combinations_list
all_combinations = all_combinations[1:]
for item in all_combinations:
    if(len(item) >= min_layer and len(item) <= max_layer):
        dil_list.append(list(item))

param_dict = {
    'nb_filters': range(2,64),
    'kernel_size': range(2,16),
    'use_skip_connections': [True, False],
    'dil_list': dil_list
}

def objfunc(args_list):

    objective_evaluated = []
    
    start_time = time.time()
    
    for hyper_par in args_list:
        nb_filters = hyper_par['nb_filters']
        kernel_size = hyper_par['kernel_size']
        use_skip_connections = hyper_par['use_skip_connections']
        dil_list = hyper_par['dil_list']
            
        objective = objective_NN(epochs=model_epochs,nb_filters=nb_filters,kernel_size=kernel_size,
                                 dilations=dil_list,use_skip_connections=use_skip_connections,)
        objective_evaluated.append(objective)
        
        end_time = time.time()
        print('objective:', objective, ' time:',end_time-start_time)
        
    return objective_evaluated

conf_Dict = dict()
conf_Dict['batch_size'] = 1 
conf_Dict['num_iteration'] = NAS_epochs
conf_Dict['initial_random']= 5
tuner = Tuner(param_dict, objfunc,conf_Dict)
all_runs = []
results = tuner.maximize()
all_runs.append(results)
save_res(all_runs,log_file_name[0:-4]+'.p')

x.shape= (None, 45)
model.x = (None, 550, 6)
model.y = (None, 9)
Instructions for updating:
Use `tf.compat.v1.graph_util.tensor_shape_from_node_def_name`

=========================Options=============================
-max_depth                  10000
-min_bytes                  0
-min_peak_bytes             0
-min_residual_bytes         0
-min_output_bytes           0
-min_micros                 0
-min_accelerator_micros     0
-min_cpu_micros             0
-min_params                 0
-min_float_ops              1
-min_occurrence             0
-step                       -1
-order_by                   float_ops
-account_type_regexes       .*
-start_name_regexes         .*
-trim_name_regexes          
-show_name_regexes          .*
-hide_name_regexes          
-account_displayed_op_only  true
-select                     float_ops
-output                     stdout:

==================Model Analysis Report======================

Doc:
scope: The nodes in the model graph are organized by 

INFO:tensorflow:Assets written to: /tmp/tmpq78w3twv/assets


INFO:tensorflow:Assets written to: /tmp/tmpq78w3twv/assets


Design choice: [-5.0, 'inf', 'inf', 1189068.0, 1200552, 353648664, -1, 45, 11, [2, 4, 8, 16, 64, 128, 256], False]
objective: -5.0  time: 4.6496665477752686
x.shape= (None, 39)
model.x = (None, 550, 6)
model.y = (None, 9)

=========================Options=============================
-max_depth                  10000
-min_bytes                  0
-min_peak_bytes             0
-min_residual_bytes         0
-min_output_bytes           0
-min_micros                 0
-min_accelerator_micros     0
-min_cpu_micros             0
-min_params                 0
-min_float_ops              1
-min_occurrence             0
-step                       -1
-order_by                   float_ops
-account_type_regexes       .*
-start_name_regexes         .*
-trim_name_regexes          
-show_name_regexes          .*
-hide_name_regexes          
-account_displayed_op_only  true
-select                     float_ops
-output                     stdout:

==================Model Analysis Report==============

INFO:tensorflow:Assets written to: /tmp/tmps1qdzxrm/assets


...


Epoch 00435: val_accuracy did not improve from 0.89200
Epoch 436/500
428/428 [==============================] - 2s 6ms/step - loss: 0.1471 - accuracy: 0.9508 - val_loss: 0.6816 - val_accuracy: 0.8820

Epoch 00436: val_accuracy did not improve from 0.89200
Epoch 437/500
428/428 [==============================] - 2s 6ms/step - loss: 0.1340 - accuracy: 0.9548 - val_loss: 0.7393 - val_accuracy: 0.8820

Epoch 00437: val_accuracy did not improve from 0.89200
Epoch 438/500
428/428 [==============================] - 2s 6ms/step - loss: 0.1372 - accuracy: 0.9536 - val_loss: 0.7307 - val_accuracy: 0.8730

Epoch 00438: val_accuracy did not improve from 0.89200
Epoch 439/500
428/428 [==============================] - 2s 6ms/step - loss: 0.1288 - accuracy: 0.9571 - val_loss: 0.7632 - val_accuracy: 0.8800

Epoch 00439: val_accuracy did not improve from 0.89200
Epoch 440/500
428/428 [==============================] - 2s 6ms/step - loss: 0.1416 - accuracy: 0.9506 - val_loss: 0.7467 - val_accuracy: 0.


 38%|███████████████▍                        | 385/1000 [00:26<00:40, 15.03it/s]


 77%|██████████████████████████████▉         | 773/1000 [00:52<00:15, 14.33it/s]


100%|███████████████████████████████████████| 1000/1000 [01:09<00:00, 14.49it/s]


Design choice: [-0.5297095090734862, 0.10500001907348633, 0.193, 73708.0, 77416, 18309414, -1, 20, 5, [1, 2, 32, 256], True]
objective: -0.5297095090734862  time: 1289.52978181839


In [ ]:
input_dim=X_tr.shape[2]

model = compiled_tcn(return_sequences=False,
                     num_feat=input_dim,
                     num_classes=Y_tr.shape[1],
                     nb_filters=results['best_params']['nb_filters'],
                     kernel_size=results['best_params']['kernel_size'],
                     dilations=results['best_params']['dil_list'],
                     nb_stacks=1,
                     max_len=window_size,
                     use_weight_norm=False,
                     use_skip_connections=results['best_params']['use_skip_connections'])

opt = tf.keras.optimizers.Adam()
model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
              optimizer=opt,metrics=['accuracy'])

checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
          epochs=model_epochs,callbacks=[checkpoint],shuffle=True,verbose=1)

model = load_model(model_name,custom_objects={'TCN': TCN})
test_accu = model.evaluate(x=X_test,y=Y_test)[1]
print('Test Accuracy:', test_accu)
adv_accu = perform_fgsm_attack(data=X_test, lab=Y_test,eps=epsilon,my_model=model)
print('Adversarial Accuracy:', adv_accu)

x.shape= (None, 11)
model.x = (None, 550, 6)
model.y = (None, 9)
Epoch 1/500
428/428 [==============================] - 4s 7ms/step - loss: 12.7817 - accuracy: 0.1879 - val_loss: 4.8855 - val_accuracy: 0.2740

Epoch 00001: val_accuracy improved from -inf to 0.27400, saving model to Auritus_advNUCLEO_F446RE.hdf5
Epoch 2/500
428/428 [==============================] - 3s 6ms/step - loss: 3.7263 - accuracy: 0.2729 - val_loss: 2.5054 - val_accuracy: 0.3080

Epoch 00002: val_accuracy improved from 0.27400 to 0.30800, saving model to Auritus_advNUCLEO_F446RE.hdf5
Epoch 3/500
428/428 [==============================] - 3s 6ms/step - loss: 2.2612 - accuracy: 0.3059 - val_loss: 1.8957 - val_accuracy: 0.3320

Epoch 00003: val_accuracy improved from 0.30800 to 0.33200, saving model to Auritus_advNUCLEO_F446RE.hdf5
Epoch 4/500
428/428 [==============================] - 3s 6ms/step - loss: 1.8029 - accuracy: 0.3540 - val_loss: 1.6712 - val_accuracy: 0.3830

Epoch 00004: val_accuracy improved from 0.3